# Business Problem

A set of methods and algorithms known as recommender systems enable users to be suggested "relevant" stuff. The suggested things should ideally be as pertinent to the user as feasible so that the user will interact with them. Typically, the suggestions refer to various decision-making processes, such as what product to purchase, what music to listen to, or what online news to read. Recommender systems are particularly useful when an individual needs to choose an item from a potentially overwhelming number of items that a service may offer.

Click to learn more about: [Recommender Systems](https://en.wikipedia.org/wiki/Recommender_system)

One approach to the design of recommender systems that has wide use is **collaborative filtering**. Collaborative filtering is based on the assumption that people who agreed in the past will agree in the future, and that they will like similar kinds of items as they liked in the past. The system generates recommendations using only information about rating profiles for different users or items.

**Item-based**, or item-to-item, is a form of collaborative filtering for recommender systems based on the similarity between items calculated using people's ratings of those items. Item-item collaborative filtering was invented and used by Amazon.com in 1998.

**User-Based Collaborative Filtering** is a technique used to predict the items that a user might like on the basis of ratings given to that item by the other users who have similar taste with that of the target user.

**Matrix factorization algorithms** work by decomposing the user-item interaction matrix into the product of two lower dimensionality rectangular matrices. The prediction results can be improved by assigning different regularization weights to the latent factors based on items' popularity and users' activeness.

Make 10 movie recommendations for the user whose ID is given, using the item-based and user-based recommender methods.

The dataset was provided by MovieLens, a movie recommendation service. It contains the rating scores for these movies along with the movies. It contains 2,000,0263 ratings across 27,278 movies. This data set was created on October 17, 2016. Includes 138,493 users and data from 09 January 1995 to 31 March 2015. Users are randomly selected. It is known that all selected users voted for at least 20 movies.

**movie.csv**
* movieId: Unique movie number.
* title: Movie name
* genres: Movie genres

**rating.csv**
* userid: Unique user number. (UniqueID)
* movieId: Unique movie number.
* rating: Rating given to the movie by the user
* timestamp: Evaluation date

# Data Preprocessing

In [58]:
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.width', 500)
pd.set_option('display.expand_frame_repr', False)
import plotly.express as px
from pandas_profiling import ProfileReport
from plotly.subplots import make_subplots
import plotly.graph_objects as go
from surprise import Reader, SVD, Dataset, accuracy
from surprise.model_selection import GridSearchCV, train_test_split, cross_validate

In [2]:
def check_df(dataframe, head=10):
    print("##################### Head #####################")
    print(dataframe.head(head))
    print("##################### Variables #####################")
    print(dataframe.columns)
    print("##################### Descriptive Stats #####################")
    print(dataframe.describe().T)
    print("##################### Null Values #####################")
    print(dataframe.isnull().sum())
    print("##################### Types #####################")
    print(dataframe.dtypes)
    print("##################### Shape #####################")
    print(dataframe.shape)
    print("##################### Info #####################")
    print(dataframe.info())

In [3]:
movie = pd.read_csv('../input/movie-rating-datasets/movie.csv')
rating = pd.read_csv('../input/movie-rating-datasets/rating.csv')

In [4]:
check_df(movie)

##################### Head #####################
   movieId                               title                                       genres
0        1                    Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy
1        2                      Jumanji (1995)                   Adventure|Children|Fantasy
2        3             Grumpier Old Men (1995)                               Comedy|Romance
3        4            Waiting to Exhale (1995)                         Comedy|Drama|Romance
4        5  Father of the Bride Part II (1995)                                       Comedy
5        6                         Heat (1995)                        Action|Crime|Thriller
6        7                      Sabrina (1995)                               Comedy|Romance
7        8                 Tom and Huck (1995)                           Adventure|Children
8        9                 Sudden Death (1995)                                       Action
9       10                    G

In [5]:
check_df(rating)

##################### Head #####################
   userId  movieId  rating            timestamp
0       1        2     3.5  2005-04-02 23:53:47
1       1       29     3.5  2005-04-02 23:31:16
2       1       32     3.5  2005-04-02 23:33:39
3       1       47     3.5  2005-04-02 23:32:07
4       1       50     3.5  2005-04-02 23:29:40
5       1      112     3.5  2004-09-10 03:09:00
6       1      151     4.0  2004-09-10 03:08:54
7       1      223     4.0  2005-04-02 23:46:13
8       1      253     4.0  2005-04-02 23:35:40
9       1      260     4.0  2005-04-02 23:33:46
##################### Variables #####################
Index(['userId', 'movieId', 'rating', 'timestamp'], dtype='object')
##################### Descriptive Stats #####################
              count          mean           std  min      25%      50%       75%       max
userId   20000263.0  69045.872583  40038.626653  1.0  34395.0  69141.0  103637.0  138493.0
movieId  20000263.0   9041.567330  19789.477445  1.0    9

In [6]:
profile = ProfileReport(rating, title="Pandas Profiling Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [7]:
df = movie.merge(rating, how="left", on="movieId")
df.head()

movieId             title                                       genres  userId  rating            timestamp
0        1  Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy     3.0     4.0  1999-12-11 13:36:47
1        1  Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy     6.0     5.0  1997-03-13 17:50:52
2        1  Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy     8.0     4.0  1996-06-05 13:37:51
3        1  Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy    10.0     4.0  1999-11-25 02:44:47
4        1  Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy    11.0     4.5  2009-01-02 01:13:41

In [8]:
comment_counts = pd.DataFrame(df["title"].value_counts())

In [9]:
rare_movies = comment_counts[comment_counts["title"] <= 1000].index
common_movies = df[~df["title"].isin(rare_movies)]

In [12]:
popular_movies = common_movies["title"].value_counts().head(20)

In [33]:
popular_movies_by_ratings = common_movies.groupby("title").agg({"rating": "sum"}).reset_index()

In [34]:
popular_movies_by_ratings["all"] = "all"
fig = px.treemap(popular_movies_by_ratings.head(20), path=["all", 'title'], 
                 values='rating', color=popular_movies_by_ratings["rating"].head(20), hover_data=["title"])
fig.update_layout(margin = dict(t=50, l=25, r=25, b=25))
fig.show()

In [15]:
fig = go.Figure(go.Bar(
            x=popular_movies.values,
            y=popular_movies.index,
            orientation='h'))

fig.show()

In [16]:
user_movie_df = common_movies.pivot_table(index=["userId"], columns=["title"], values="rating")

In [17]:
user_movie_df.head(10)

title   'burbs, The (1989)  (500) Days of Summer (2009)  *batteries not included (1987)  ...And Justice for All (1979)  10 Things I Hate About You (1999)  10,000 BC (2008)  101 Dalmatians (1996)  101 Dalmatians (One Hundred and One Dalmatians) (1961)  102 Dalmatians (2000)  12 Angry Men (1957)  12 Years a Slave (2013)  127 Hours (2010)  13 Going on 30 (2004)  13th Warrior, The (1999)  1408 (2007)  15 Minutes (2001)  16 Blocks (2006)  17 Again (2009)  1984 (Nineteen Eighty-Four) (1984)  2 Days in the Valley (1996)  2 Fast 2 Furious (Fast and the Furious 2, The) (2003)  20,000 Leagues Under the Sea (1954)  200 Cigarettes (1999)  2001: A Space Odyssey (1968)  2010: The Year We Make Contact (1984)  2012 (2009)  2046 (2004)  21 (2008)  21 Grams (2003)  21 Jump Street (2012)  24 Hour Party People (2002)  25th Hour (2002)  27 Dresses (2008)  28 Days (2000)  28 Days Later (2002)  28 Weeks Later (2007)  3 Ninjas (1992)  3-Iron (Bin-jip) (2004)  30 Days of Night (2007)  300 (2007)  3000 Miles to Graceland (2001)  39 Steps, The (1935)  3:10 to Yuma (2007)  40 Days and 40 Nights (2002)  40-Year-Old Virgin, The (2005)  400 Blows, The (Les quatre cents coups) (1959)  42 Up (1998)  48 Hrs. (1982)  50 First Dates (2004)  50/50 (2011)  54 (1998)  6th Day, The (2000)  7th Voyage of Sinbad, The (1958)  8 1/2 (8½) (1963)  8 Heads in a Duffel Bag (1997)  8 Mile (2002)  8MM (1999)  9 (2009)  9 1/2 Weeks (Nine 1/2 Weeks) (1986)  A-Team, The (2010)  A.I. Artificial Intelligence (2001)  AVP: Alien vs. Predator (2004)  AVPR: Aliens vs. Predator - Requiem (2007)  About Last Night... (1986)  About Schmidt (2002)  About a Boy (2002)  Absent-Minded Professor, The (1961)  Absolute Power (1997)  Abyss, The (1989)  Accepted (2006)  Accidental Tourist, The (1988)  Accused, The (1988)  Ace Ventura: Pet Detective (1994)  Ace Ventura: When Nature Calls (1995)  Across the Universe (2007)  Adaptation (2002)  Addams Family Values (1993)  Addams Family, The (1991)  Addicted to Love (1997)  Adjustment Bureau, The (2011)  Adventureland (2009)  Adventures in Babysitting (1987)  Adventures of Baron Munchausen, The (1988)  Adventures of Buckaroo Banzai Across the 8th Dimension, The (1984)  Adventures of Milo and Otis, The (Koneko monogatari) (1986)  Adventures of Pinocchio, The (1996)  Adventures of Priscilla, Queen of the Desert, The (1994)  Adventures of Robin Hood, The (1938)  Adventures of Rocky and Bullwinkle, The (2000)  Adventures of Tintin, The (2011)  Aeon Flux (2005)  Affair to Remember, An (1957)  Affliction (1997)  African Queen, The (1951)  After Hours (1985)  Age of Innocence, The (1993)  Agnes of God (1985)  Aguirre: The Wrath of God (Aguirre, der Zorn Gottes) (1972)  Air America (1990)  Air Bud (1997)  Air Force One (1997)  Airheads (1994)  Airplane II: The Sequel (1982)  Airplane! (1980)  Airport (1970)  Akira (1988)  Aladdin (1992)  Aladdin and the King of Thieves (1996)  Alexander (2004)  Alfie (2004)  Ali (2001)  Alice in Wonderland (1951)  Alice in Wonderland (2010)  Alien (1979)  Alien Nation (1988)  Alien: Resurrection (1997)  Aliens (1986)  Alien³ (a.k.a. Alien 3) (1992)  Alive (1993)  All About Eve (1950)  All About My Mother (Todo sobre mi madre) (1999)  All Dogs Go to Heaven (1989)  All Dogs Go to Heaven 2 (1996)  All Quiet on the Western Front (1930)  All That Jazz (1979)  All the President's Men (1976)  All the Pretty Horses (2000)  Almost Famous (2000)  Along Came Polly (2004)  Along Came a Spider (2001)  Alphaville (Alphaville, une étrange aventure de Lemmy Caution) (1965)  Altered States (1980)  Always (1989)  Amadeus (1984)  Amateur (1994)  Amazing Spider-Man, The (2012)  Amelie (Fabuleux destin d'Amélie Poulain, Le) (2001)  America's Sweethearts (2001)  American Beauty (1999)  American Gangster (2007)  American Gigolo (1980)  American Graffiti (1973)  American History X (1998)  American Hustle (2013)  American Movie (1999)  American Pie (1999)  American Pie 2 (2001)  American President, The (1995)  American Psycho (2000)  American Splendo

## User-Based Collaborative Filtering

In [18]:
random_user = int(pd.Series(user_movie_df.index).sample(1, random_state=45).values)
random_user_df = user_movie_df[user_movie_df.index == random_user]
movies_watched = random_user_df.columns[random_user_df.notna().any()].tolist()

In [21]:
movies_watched # by random user

['Ace Ventura: Pet Detective (1994)',
 'Ace Ventura: When Nature Calls (1995)',
 'Aladdin (1992)',
 'American President, The (1995)',
 'Apollo 13 (1995)',
 'Babe (1995)',
 'Bullets Over Broadway (1994)',
 'Clueless (1995)',
 'Disclosure (1994)',
 'Forrest Gump (1994)',
 'Four Weddings and a Funeral (1994)',
 'Home Alone (1990)',
 'Jurassic Park (1993)',
 'Like Water for Chocolate (Como agua para chocolate) (1992)',
 'Little Women (1994)',
 "Mr. Holland's Opus (1995)",
 'Mrs. Doubtfire (1993)',
 'Much Ado About Nothing (1993)',
 "Muriel's Wedding (1994)",
 'Nine Months (1995)',
 'Operation Dumbo Drop (1995)',
 'Piano, The (1993)',
 'Postman, The (Postino, Il) (1994)',
 'Ready to Wear (Pret-A-Porter) (1994)',
 'Remains of the Day, The (1993)',
 'Sabrina (1995)',
 "Schindler's List (1993)",
 'Secret Garden, The (1993)',
 'Sense and Sensibility (1995)',
 'Shadowlands (1993)',
 'Silence of the Lambs, The (1991)',
 'Star Trek: Generations (1994)',
 'Stargate (1994)']

In [19]:
movies_watched_df = user_movie_df[movies_watched]

In [20]:
movies_watched_df

title     Ace Ventura: Pet Detective (1994)  Ace Ventura: When Nature Calls (1995)  Aladdin (1992)  American President, The (1995)  Apollo 13 (1995)  Babe (1995)  Bullets Over Broadway (1994)  Clueless (1995)  Disclosure (1994)  Forrest Gump (1994)  Four Weddings and a Funeral (1994)  Home Alone (1990)  Jurassic Park (1993)  Like Water for Chocolate (Como agua para chocolate) (1992)  Little Women (1994)  Mr. Holland's Opus (1995)  Mrs. Doubtfire (1993)  Much Ado About Nothing (1993)  Muriel's Wedding (1994)  Nine Months (1995)  Operation Dumbo Drop (1995)  Piano, The (1993)  Postman, The (Postino, Il) (1994)  Ready to Wear (Pret-A-Porter) (1994)  Remains of the Day, The (1993)  Sabrina (1995)  Schindler's List (1993)  Secret Garden, The (1993)  Sense and Sensibility (1995)  Shadowlands (1993)  Silence of the Lambs, The (1991)  Star Trek: Generations (1994)  Stargate (1994)
userId                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               
1.0                                     NaN                                    NaN             NaN                             NaN               NaN          NaN                           NaN              NaN                NaN                  NaN                                 NaN                NaN                   NaN                                                NaN                           NaN                        NaN                    NaN                            NaN                      NaN                 NaN                          NaN                NaN                                NaN                                   NaN                             NaN             NaN                      NaN                        NaN                           NaN                 NaN                               3.5                            NaN              NaN
2.0                                     NaN                                    NaN             NaN                             NaN               NaN          NaN                           NaN              NaN                NaN                  NaN                                 NaN                NaN                   5.0                                                NaN                           NaN                        5.0                    NaN                            NaN                      NaN                 NaN                          NaN                NaN                                NaN                                   NaN                             NaN             NaN                      NaN                        NaN                           NaN                 NaN                               NaN                            NaN              NaN
3.0                                     NaN                                    NaN             NaN                             NaN               NaN          NaN                           NaN              NaN                NaN                  NaN                                 NaN                NaN                   5.0                                                NaN                           NaN                        NaN                    NaN

In [22]:
user_movie_count = movies_watched_df.T.notnull().sum()
user_movie_count

In [24]:
user_movie_count = user_movie_count.reset_index()
user_movie_count.columns = ["userId", "movie_count"]
# We filter out users who have watched at least 60% of the same movie as the random user.
perc = len(movies_watched) * 60 / 100
users_same_movies = user_movie_count[user_movie_count["movie_count"] > perc]["userId"]

In [26]:
final_df = pd.concat([movies_watched_df[movies_watched_df.index.isin(users_same_movies)],
                      random_user_df[movies_watched]])

In [27]:
final_df

title     Ace Ventura: Pet Detective (1994)  Ace Ventura: When Nature Calls (1995)  Aladdin (1992)  American President, The (1995)  Apollo 13 (1995)  Babe (1995)  Bullets Over Broadway (1994)  Clueless (1995)  Disclosure (1994)  Forrest Gump (1994)  Four Weddings and a Funeral (1994)  Home Alone (1990)  Jurassic Park (1993)  Like Water for Chocolate (Como agua para chocolate) (1992)  Little Women (1994)  Mr. Holland's Opus (1995)  Mrs. Doubtfire (1993)  Much Ado About Nothing (1993)  Muriel's Wedding (1994)  Nine Months (1995)  Operation Dumbo Drop (1995)  Piano, The (1993)  Postman, The (Postino, Il) (1994)  Ready to Wear (Pret-A-Porter) (1994)  Remains of the Day, The (1993)  Sabrina (1995)  Schindler's List (1993)  Secret Garden, The (1993)  Sense and Sensibility (1995)  Shadowlands (1993)  Silence of the Lambs, The (1991)  Star Trek: Generations (1994)  Stargate (1994)
userId                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               
91.0                                    2.5                                    2.0             NaN                             4.0               3.5          NaN                           NaN              NaN                NaN                  4.0                                 4.5                3.0                   3.5                                                NaN                           3.5                        3.5                    4.0                            4.0                      3.5                 2.5                          2.5                NaN                                NaN                                   NaN                             NaN             2.5                      4.5                        NaN                           NaN                 NaN                               3.0                            3.5              4.0
130.0                                   4.0                                    3.0             NaN                             3.0               3.0          NaN                           NaN              3.0                5.0                  5.0                                 5.0                3.0                   4.0                                                3.0                           NaN                        4.0                    4.0                            NaN                      3.0                 NaN                          NaN                4.0                                4.0                                   NaN                             3.0             NaN                      5.0                        NaN                           NaN                 3.0                               5.0                            NaN              3.0
156.0                                   3.0                                    NaN             NaN                             5.0               5.0          3.0                           NaN              NaN                4.0                  5.0                                 3.0                4.0                   5.0                                                NaN                           NaN                        4.0                    5.0

In [28]:
# User rating correlations
corr_df = final_df.T.corr().unstack().sort_values().drop_duplicates()

corr_df = pd.DataFrame(corr_df, columns=["corr"])

corr_df.index.names = ['user_id_1', 'user_id_2']

corr_df = corr_df.reset_index()

corr_df

user_id_1  user_id_2      corr
0         105664.0    78262.0 -0.954490
1         119715.0    55005.0 -0.952579
2         104652.0   137558.0 -0.950000
3          72596.0    29398.0 -0.939060
4          28866.0    67756.0 -0.936065
...            ...        ...       ...
5556788    69856.0    15366.0  0.978167
5556789   111108.0   117465.0  1.000000
5556790    28941.0    28941.0  1.000000
5556791    16562.0    41005.0  1.000000
5556792       91.0    16562.0       NaN

[5556793 rows x 3 columns]

Now that we found a correlation between users' ratings, we can recommend a film to our random user based on the user's liking behavior.

In [35]:
top_users = corr_df[(corr_df["user_id_1"] == random_user) & (corr_df["corr"] >= 0.65)][
    ["user_id_2", "corr"]].reset_index(drop=True)

top_users = top_users.sort_values(by='corr', ascending=False)

top_users.rename(columns={"user_id_2": "userId"}, inplace=True)

In [38]:
top_users_ratings = top_users.merge(rating[["userId", "movieId", "rating"]], how='inner')

top_users_ratings = top_users_ratings[top_users_ratings["userId"] != random_user]

In [49]:
top_users_ratings.sort_values("corr", ascending=False).head(10).style.background_gradient(subset= "corr", cmap='Reds')

Just looking at the correlation will not be enough for a movie recommendation. At the same time, weighting the scores and correlations given by users will give a more accurate result.

In [43]:
top_users_ratings['weighted_rating'] = top_users_ratings['corr'] * top_users_ratings['rating']
recommendation_df = top_users_ratings.groupby('movieId').agg({"weighted_rating": "mean"})
recommendation_df = recommendation_df.reset_index()
movies_to_be_recommend = recommendation_df[recommendation_df["weighted_rating"] > 3.5].sort_values("weighted_rating", ascending=False).iloc[0:5]
movies_to_be_recommend = movies_to_be_recommend.merge(movie[["movieId", "title"]])
movies_to_be_recommend[~movies_to_be_recommend.movieId.isin(movies_watched)]
# 5 movies recommended.

movieId  weighted_rating                              title
0     1922          3.76358                    Whatever (1998)
1     2057          3.76358     Incredible Journey, The (1963)
2     2077          3.76358  Journey of Natty Gann, The (1985)
3     2485          3.76358              She's All That (1999)
4     2577          3.76358                   Metroland (1997)

## Item-Based Recommendation

In [52]:
# Random user chosen
user = 108170

Choose the latest movie that has highest rating user gave

In [53]:
movie_id = rating[(rating["userId"] == user) & (rating["rating"] == 5.0)].sort_values(by="timestamp", ascending=False)["movieId"][0:1].values[0]
movie_name = movie[movie["movieId"] == movie_id]["title"].values[0]

In [55]:
movie_name = user_movie_df[movie_name]
user_movie_df.corrwith(movie_name).sort_values(ascending=False).head(10)

title
Wild at Heart (1990)                     1.000000
My Science Project (1985)                0.570187
Mediterraneo (1991)                      0.538868
Old Man and the Sea, The (1958)          0.536192
National Lampoon's Senior Trip (1995)    0.533029
Clockwatchers (1997)                     0.483337
Repo Man (1984)                          0.478674
Lost Highway (1997)                      0.476251
Blue Velvet (1986)                       0.471225
Jeffrey (1995)                           0.457849
dtype: float64

In [56]:
# choose based on correlation of ratings
user_movie_df.corrwith(movie_name).sort_values(ascending=False).iloc[1:6]
# 5 movies recommended.

title
My Science Project (1985)                0.570187
Mediterraneo (1991)                      0.538868
Old Man and the Sea, The (1958)          0.536192
National Lampoon's Senior Trip (1995)    0.533029
Clockwatchers (1997)                     0.483337
dtype: float64

## Matrix Factorization

We are preparing the dataset. We will then estimate the missing ratings with latent variables. For more detailed information: [Matrix Factorization](https://en.wikipedia.org/wiki/Matrix_factorization_(recommender_systems))

In [59]:
movie_ids = [130219, 356, 4422, 541]
sample_df = df[df.movieId.isin(movie_ids)]
sample_df.head()

movieId                title                    genres  userId  rating            timestamp
2457839      356  Forrest Gump (1994)  Comedy|Drama|Romance|War     4.0     4.0  1996-08-24 09:28:42
2457840      356  Forrest Gump (1994)  Comedy|Drama|Romance|War     7.0     4.0  2002-01-16 19:02:55
2457841      356  Forrest Gump (1994)  Comedy|Drama|Romance|War     8.0     5.0  1996-06-05 13:44:19
2457842      356  Forrest Gump (1994)  Comedy|Drama|Romance|War     9.0     4.0  2001-07-01 20:26:38
2457843      356  Forrest Gump (1994)  Comedy|Drama|Romance|War    10.0     3.0  1999-11-25 02:32:02

In [60]:
reader = Reader(rating_scale=(1, 5))
data = Dataset.load_from_df(sample_df[['userId',
                                       'movieId',
                                       'rating']], reader)

### Modeling

In [61]:
trainset, testset = train_test_split(data, test_size=.25)
svd_model = SVD()
svd_model.fit(trainset)
predictions = svd_model.test(testset)

accuracy.rmse(predictions)

RMSE: 0.9292


0.9292286458672081

In [62]:
svd_model.predict(uid=1.0, iid=356, verbose=True)

user: 1.0        item: 356        r_ui = None   est = 4.03   {'was_impossible': False}


Prediction(uid=1.0, iid=356, r_ui=None, est=4.02819800207791, details={'was_impossible': False})

### Model Tuning

In [63]:
param_grid = {'n_epochs': [5, 10, 20],
              'lr_all': [0.002, 0.005, 0.007]}


gs = GridSearchCV(SVD,
                  param_grid,
                  measures=['rmse', 'mae'],
                  cv=3,
                  n_jobs=-1,
                  joblib_verbose=True)

gs.fit(data)

print(gs.best_score['rmse'])
print(gs.best_params['rmse'])

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.


0.9303005959096943
{'n_epochs': 5, 'lr_all': 0.002}


[Parallel(n_jobs=-1)]: Done  27 out of  27 | elapsed:  1.2min finished


In the last stage, the learning process is performed with the best parameters by considering the whole data set. As an example, not many hyperparameters have been optimized, a simple **hyperparameter optimization** has been done in the beginning.

In [64]:
svd_model = SVD(**gs.best_params['rmse'])

data = data.build_full_trainset()
svd_model.fit(data)

svd_model.predict(uid=1.0, iid=356, verbose=True)

user: 1.0        item: 356        r_ui = None   est = 4.08   {'was_impossible': False}


Prediction(uid=1.0, iid=356, r_ui=None, est=4.077231190142465, details={'was_impossible': False})